In [1]:
# 라이브러리 설치
import pandas as pd
import numpy as np
from pprint import pprint
import pickle
from tqdm import tqdm_notebook
from time import time
import os

from gensim import corpora
from gensim.models import AuthorTopicModel
from gensim.models import CoherenceModel
from gensim.corpora import Dictionary, bleicorpus # bleicorpus는 저장을 하기 위한 용도일 뿐임

# 사용자간의 유사성을 평가하기 위한 measure를 사용하기 위해 불러오기
# 어떤 두 개의 확률분포의 차이를 보겠다
from gensim.matutils import hellinger
from gensim import matutils


# 1. 데이터 불러오기

In [2]:
path_df_final = r"C:\Users\user\Desktop\새 폴더\data\빅카인즈_통합_final.xlsx"

In [3]:
data = pd.read_excel(path_df_final, index_col=False)
data.reset_index(drop=True, inplace=True)


In [4]:
data

Author                                              Title  \
0        목포                 [사설] 생활권 침해 없는데 봉안당 불허···님비에 법원 제동   
1        목포                       “학생 수 감소했다면 학교용지비용 부담 필요 없어”   
2        목포           경단녀서 꽃가게 사장님으로… "지방은 기회의 공간" [지방시대 지방영웅]   
3        목포              장수군장애인탁구단 이근우 선수 "장애는 불편할 뿐 불행한 것 아냐”   
4        목포                         전남도, 청소년 지원 종합 거점공간 23일 개청   
...     ...                                                ...   
4532     신안                      신년특집>"딸기 엉글때 청년농 '농촌의 희망' 될터"   
4533     신안             새해특집>신안팔금면 딸기농장, 청년농업인 교육…"군수님 역점사업이죠"   
4534     신안                   새해특집>"스마트 딸기 재배기술로 청년농업인 우상 될래요"   
4535     신안                                     [신년사] 김종식 목포시장   
4536     신안  [포토] 노행식 국제로타리 3640지구 총재, 2021년에도 인류의 희망이 되는 봉...   

                                                Content  \
0     극단적인 지역이기주의에 지역 현안들이 발목이 잡혀있는 가운데 법원이 과도한 님비현상...   
1     [KBS 광주]\n취학 인구가 감소했는데도 학교용지부담금을 부과한 행정처분은 부당하...   
2     <4> 전남 목포 '두리하나 플라워' 임효백씨 아이 때문에 결심한 '지방살이'서 꿈...   
3     항저우아시안게임 메달 이근우 선수\n“만약 세상에 즐거움만 있다면 우리는 결코 인내...   
4     전남청소년미래재단 상담·안전망 구축·자기개발 기회 제공 등 종합 지원 거점 공연장·...   
...                                                 ...   
4532  청년농부가 미래다=신안 딸기학교 교육생\n지난달 천사섬 딸기영농조합법인을 출범시킨 ...   
4533  청년농 실패 최소화…연중 딸기 생산 가능\n청년 예비농부 5명이 입학한 신안 팔금면...   
4534  청년농부가 미래다=신안 딸기학교 교육생 5명\n지난달 천사섬 딸기영농조합법인을 출범...   
4535  김종식 목포시장\n존경하는 시민 여러분! 그리고 동료 공직자 여러분! 2021년 새...   
4536  효송 노행식 국제로타리 3640 지구 총재는 온라인으로 발표한 신년사를 통해 “20...   

                                        Extracted_Nouns  
0     극단 지역 이기주의 지역 현안 발목 가운데 법원 과도 님비 현상 제동 향후 님비 현...  
1     취학 인구 감소 학교 용지 부담금 부과 행정 처분 부당 판결 행정부 지역 주택 조합...  
2     두리하나 플라워 아이 결심 지방 살 서 꿈 청년 공간 다양 창업 기회 제공 시작 때...  
3     아시안 게임 메달 선수 세상 즐거움 인내 법 장애 불편 불행 장애인 체육회 탁구 선...  
4     청소년 미래 재단 상담 안전 망 구축 자기 개발 기회 제공 종합 지원 거점 공연장 ...  
...                                                 ...  
4532  청년 농부 미래 딸기 학교 교육 지난달 천사 섬 딸기 영농 조합 법인 출범 왼쪽 대...  
4533  청년 농 실패 최소 연중 딸기 생산 가능 청년 예비 농부 입학 딸기 농장 청년 농업...  
4534  청년 농부 미래 딸기 학교 교육 지난달 천사 섬 딸기 영농 조합 법인 출범 왼쪽 대...  
4535  시장 존경 시민 동료 공직자 새해 소원 성취 복 해 기원 해 발전 성원 지지 시민 ...  
4536  국제 로타리 지구 총재 온라인 발표 신년사 새해 사회 거리 코로나 인류 고통 마음 ...  

[4537 rows x 4 columns]

In [5]:
data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 4537 entries, 0 to 4536
Data columns (total 4 columns):
 #   Column           Non-Null Count  Dtype 
---  ------           --------------  ----- 
 0   Author           4537 non-null   object
 1   Title            4537 non-null   object
 2   Content          4537 non-null   object
 3   Extracted_Nouns  4537 non-null   object
dtypes: object(4)
memory usage: 141.9+ KB


In [6]:
# 결측값이 있는 행 제거
data = data.dropna(axis=0)
data

Author                                              Title  \
0        목포                 [사설] 생활권 침해 없는데 봉안당 불허···님비에 법원 제동   
1        목포                       “학생 수 감소했다면 학교용지비용 부담 필요 없어”   
2        목포           경단녀서 꽃가게 사장님으로… "지방은 기회의 공간" [지방시대 지방영웅]   
3        목포              장수군장애인탁구단 이근우 선수 "장애는 불편할 뿐 불행한 것 아냐”   
4        목포                         전남도, 청소년 지원 종합 거점공간 23일 개청   
...     ...                                                ...   
4532     신안                      신년특집>"딸기 엉글때 청년농 '농촌의 희망' 될터"   
4533     신안             새해특집>신안팔금면 딸기농장, 청년농업인 교육…"군수님 역점사업이죠"   
4534     신안                   새해특집>"스마트 딸기 재배기술로 청년농업인 우상 될래요"   
4535     신안                                     [신년사] 김종식 목포시장   
4536     신안  [포토] 노행식 국제로타리 3640지구 총재, 2021년에도 인류의 희망이 되는 봉...   

                                                Content  \
0     극단적인 지역이기주의에 지역 현안들이 발목이 잡혀있는 가운데 법원이 과도한 님비현상...   
1     [KBS 광주]\n취학 인구가 감소했는데도 학교용지부담금을 부과한 행정처분은 부당하...   
2     <4> 전남 목포 '두리하나 플라워' 임효백씨 아이 때문에 결심한 '지방살이'서 꿈...   
3     항저우아시안게임 메달 이근우 선수\n“만약 세상에 즐거움만 있다면 우리는 결코 인내...   
4     전남청소년미래재단 상담·안전망 구축·자기개발 기회 제공 등 종합 지원 거점 공연장·...   
...                                                 ...   
4532  청년농부가 미래다=신안 딸기학교 교육생\n지난달 천사섬 딸기영농조합법인을 출범시킨 ...   
4533  청년농 실패 최소화…연중 딸기 생산 가능\n청년 예비농부 5명이 입학한 신안 팔금면...   
4534  청년농부가 미래다=신안 딸기학교 교육생 5명\n지난달 천사섬 딸기영농조합법인을 출범...   
4535  김종식 목포시장\n존경하는 시민 여러분! 그리고 동료 공직자 여러분! 2021년 새...   
4536  효송 노행식 국제로타리 3640 지구 총재는 온라인으로 발표한 신년사를 통해 “20...   

                                        Extracted_Nouns  
0     극단 지역 이기주의 지역 현안 발목 가운데 법원 과도 님비 현상 제동 향후 님비 현...  
1     취학 인구 감소 학교 용지 부담금 부과 행정 처분 부당 판결 행정부 지역 주택 조합...  
2     두리하나 플라워 아이 결심 지방 살 서 꿈 청년 공간 다양 창업 기회 제공 시작 때...  
3     아시안 게임 메달 선수 세상 즐거움 인내 법 장애 불편 불행 장애인 체육회 탁구 선...  
4     청소년 미래 재단 상담 안전 망 구축 자기 개발 기회 제공 종합 지원 거점 공연장 ...  
...                                                 ...  
4532  청년 농부 미래 딸기 학교 교육 지난달 천사 섬 딸기 영농 조합 법인 출범 왼쪽 대...  
4533  청년 농 실패 최소 연중 딸기 생산 가능 청년 예비 농부 입학 딸기 농장 청년 농업...  
4534  청년 농부 미래 딸기 학교 교육 지난달 천사 섬 딸기 영농 조합 법인 출범 왼쪽 대...  
4535  시장 존경 시민 동료 공직자 새해 소원 성취 복 해 기원 해 발전 성원 지지 시민 ...  
4536  국제 로타리 지구 총재 온라인 발표 신년사 새해 사회 거리 코로나 인류 고통 마음 ...  

[4537 rows x 4 columns]

In [7]:
data.reset_index(drop=True, inplace=True)
data

Author                                              Title  \
0        목포                 [사설] 생활권 침해 없는데 봉안당 불허···님비에 법원 제동   
1        목포                       “학생 수 감소했다면 학교용지비용 부담 필요 없어”   
2        목포           경단녀서 꽃가게 사장님으로… "지방은 기회의 공간" [지방시대 지방영웅]   
3        목포              장수군장애인탁구단 이근우 선수 "장애는 불편할 뿐 불행한 것 아냐”   
4        목포                         전남도, 청소년 지원 종합 거점공간 23일 개청   
...     ...                                                ...   
4532     신안                      신년특집>"딸기 엉글때 청년농 '농촌의 희망' 될터"   
4533     신안             새해특집>신안팔금면 딸기농장, 청년농업인 교육…"군수님 역점사업이죠"   
4534     신안                   새해특집>"스마트 딸기 재배기술로 청년농업인 우상 될래요"   
4535     신안                                     [신년사] 김종식 목포시장   
4536     신안  [포토] 노행식 국제로타리 3640지구 총재, 2021년에도 인류의 희망이 되는 봉...   

                                                Content  \
0     극단적인 지역이기주의에 지역 현안들이 발목이 잡혀있는 가운데 법원이 과도한 님비현상...   
1     [KBS 광주]\n취학 인구가 감소했는데도 학교용지부담금을 부과한 행정처분은 부당하...   
2     <4> 전남 목포 '두리하나 플라워' 임효백씨 아이 때문에 결심한 '지방살이'서 꿈...   
3     항저우아시안게임 메달 이근우 선수\n“만약 세상에 즐거움만 있다면 우리는 결코 인내...   
4     전남청소년미래재단 상담·안전망 구축·자기개발 기회 제공 등 종합 지원 거점 공연장·...   
...                                                 ...   
4532  청년농부가 미래다=신안 딸기학교 교육생\n지난달 천사섬 딸기영농조합법인을 출범시킨 ...   
4533  청년농 실패 최소화…연중 딸기 생산 가능\n청년 예비농부 5명이 입학한 신안 팔금면...   
4534  청년농부가 미래다=신안 딸기학교 교육생 5명\n지난달 천사섬 딸기영농조합법인을 출범...   
4535  김종식 목포시장\n존경하는 시민 여러분! 그리고 동료 공직자 여러분! 2021년 새...   
4536  효송 노행식 국제로타리 3640 지구 총재는 온라인으로 발표한 신년사를 통해 “20...   

                                        Extracted_Nouns  
0     극단 지역 이기주의 지역 현안 발목 가운데 법원 과도 님비 현상 제동 향후 님비 현...  
1     취학 인구 감소 학교 용지 부담금 부과 행정 처분 부당 판결 행정부 지역 주택 조합...  
2     두리하나 플라워 아이 결심 지방 살 서 꿈 청년 공간 다양 창업 기회 제공 시작 때...  
3     아시안 게임 메달 선수 세상 즐거움 인내 법 장애 불편 불행 장애인 체육회 탁구 선...  
4     청소년 미래 재단 상담 안전 망 구축 자기 개발 기회 제공 종합 지원 거점 공연장 ...  
...                                                 ...  
4532  청년 농부 미래 딸기 학교 교육 지난달 천사 섬 딸기 영농 조합 법인 출범 왼쪽 대...  
4533  청년 농 실패 최소 연중 딸기 생산 가능 청년 예비 농부 입학 딸기 농장 청년 농업...  
4534  청년 농부 미래 딸기 학교 교육 지난달 천사 섬 딸기 영농 조합 법인 출범 왼쪽 대...  
4535  시장 존경 시민 동료 공직자 새해 소원 성취 복 해 기원 해 발전 성원 지지 시민 ...  
4536  국제 로타리 지구 총재 온라인 발표 신년사 새해 사회 거리 코로나 인류 고통 마음 ...  

[4537 rows x 4 columns]

## 1-1. 전처리 완료된 데이터 가져오기

In [8]:
data['Extracted_Nouns']

0       극단 지역 이기주의 지역 현안 발목 가운데 법원 과도 님비 현상 제동 향후 님비 현...
1       취학 인구 감소 학교 용지 부담금 부과 행정 처분 부당 판결 행정부 지역 주택 조합...
2       두리하나 플라워 아이 결심 지방 살 서 꿈 청년 공간 다양 창업 기회 제공 시작 때...
3       아시안 게임 메달 선수 세상 즐거움 인내 법 장애 불편 불행 장애인 체육회 탁구 선...
4       청소년 미래 재단 상담 안전 망 구축 자기 개발 기회 제공 종합 지원 거점 공연장 ...
                              ...                        
4532    청년 농부 미래 딸기 학교 교육 지난달 천사 섬 딸기 영농 조합 법인 출범 왼쪽 대...
4533    청년 농 실패 최소 연중 딸기 생산 가능 청년 예비 농부 입학 딸기 농장 청년 농업...
4534    청년 농부 미래 딸기 학교 교육 지난달 천사 섬 딸기 영농 조합 법인 출범 왼쪽 대...
4535    시장 존경 시민 동료 공직자 새해 소원 성취 복 해 기원 해 발전 성원 지지 시민 ...
4536    국제 로타리 지구 총재 온라인 발표 신년사 새해 사회 거리 코로나 인류 고통 마음 ...
Name: Extracted_Nouns, Length: 4537, dtype: object

In [9]:
tokenized_data=[]
for i in range(len(data)):
    row = list(data.loc[i]['Extracted_Nouns'].split(" "))
    tokenized_data.append(row)

## 1-2. Author 설정

In [10]:
author = set(data["Author"])
len(author)

3

In [11]:
# author 별 나누기(index 추출)
authors = data.groupby('Author')

In [12]:
authors.groups

{'목포': [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, ...], '무안': [1679, 1680, 1681, 1682, 1683, 1684, 1685, 1686, 1687, 1688, 1689, 1690, 1691, 1692, 1693, 1694, 1695, 1696, 1697, 1698, 1699, 1700, 1701, 1702, 1703, 1704, 1705, 1706, 1707, 1708, 1709, 1710, 1711, 1712, 1713, 1714, 1715, 1716, 1717, 1718, 1719, 1720, 1721, 1722, 1723, 1724, 1725, 1726, 1727, 1728, 1729, 1730, 1731, 1732, 1733, 1734, 1735, 1736, 1737, 1738, 1739, 1740, 1741, 1742, 1743, 1744, 1745, 1746, 1747, 1748, 1749, 1750, 1751, 1752, 1753, 1754, 1755, 1756, 1757, 1758, 1759, 1760, 1761, 1762, 1763, 1764, 1765, 1766, 1767, 1768, 1769, 1770, 1771, 1772, 1773, 1774, 1775, 1776, 1

In [13]:
type(authors.groups)

pandas.io.formats.printing.PrettyDict

In [14]:
# index로 각 지역별 뉴스기사
author2doc = {}
for user, index in authors.groups.items():
    author2doc[user] = list(index)

# 2. Author Topic Modeling

In [15]:
# ATM에 사용할 Dictionary 만들기
if not os.path.exists('./ATM/ATM_dict'):
    dictionary = corpora.Dictionary(tokenized_data)
    dictionary.save('./ATM/ATM_dict')
    print(dictionary)
else:
    dictionary = Dictionary.load('./ATM/ATM_dict')



In [16]:
# ATM에 사용할 corpus 만들기
if not os.path.exists('./ATM/ATM_corpus'):
    corpus = [dictionary.doc2bow(doc) for doc in tokenized_data]
    # BleiCorpus : pickle로 저장하는 것과 같다고 생각
    corpora.BleiCorpus.serialize('./ATM/ATM_corpus', corpus)
else:
    corpus = bleicorpus.BleiCorpus('./ATM/ATM_corpus')

In [17]:
# ATM에 들어갈 데이터 확인하기
print('Number of author: %d' % len(authors))
print('Number of unique tokens: %d' % len(dictionary))
print('Number of documents: %d' % len(corpus))

Number of author: 3
Number of unique tokens: 19722
Number of documents: 4537


In [18]:
# dictionary함수로 만든 사전에 있는 단어 보기
for idx in dictionary:
    print(dictionary[idx])

가운데
갈등
건물
건축
검토
경우
경종
과도
관계
관련
교육
균열
극단
근접
기관
기대
기피
기회
녹지
님비
묘지
문제
밀집
발목
발휘
법령
법원
변경
부당
부족
불허
비용
사실
사유
사회
상대
생활
소
소송
숙박
승소
시설
시장
신청
악영향
여건
역량
올
용도
운영
원고
의견
이기주의
이번
이용
이유
일견
자연
자체
재판부
정서
정주
정치
정치력
정치인
제기
제동
조정
주거
주목
주민
주장
지난해
지역
처분
취소
취지
침해
판결
판시
편승
학생
학습
한탕주의
해당
행동
행정부
향후
허가
현상
현안
혐오
호불호
환경
감소
감소세
계획
고려
공동
배치
부과
부담금
상당
수가
신설
용지
인구
인정
점
조합
주변
주택
증축
초등학생
취학
폭
필요
학교
행정
가게
가족
강사
강조
개발
개별
결심
결혼
경단녀
경력
경험
고객
고향
곳
공간
관계자
관리
관심
구상
궁리
귀향
극복
근무
금
금액
기자
기존
꽃
꿈
낭만
낮
냉정
다양
단절
단점
대기
대부분
대상
대출
대학
도움
돈
두리하나
디자인
때
마감
마련
마음
말
매장
메시지
멘토링
모델
모습
무늬
미소
반면
발판
밤
방법
병원
보금자리
보람
본인
봄
부지기수
부착
분야
분주
비결
비교
뿌리
사람
사례
사업
사이
사진
살
살이
삶
상경
상품
생각
서
선순환
선입견
선정
선택
선택지
설립
성공
소멸
속
손님
수준
스마트
스토어
시간
시작
신약
아이
아이디어
안내
안정
안주
어린이집
여성
연구원
영상
오후
요즘
위기
위치
유지
육아
의미
인
인건비
인식
일
일자리
입소
자리
자본
자신
장식
장점
전
전공
전문
전셋집
절대
젊은이
정답
정도
정보
정부
정착
제공
제품
존
졸업
종잣돈
주도
주위
준비
지방
지원
지원금
지원책
지자체
직원
직장인
차별
참여
창업
창업자
창출
채용
처음
청년
초기
최고
최근
축제
층
카드
코드
퇴근
퇴사
특별
특성
평가
평소
포토
플라워
플로리스트
피부
하루하루
학원
한때
한약
한의원
행사장
행안부
혁신
화분
활기
효과
후
휴대폰
희망자
힘
강자
개인전
게임
경쟁
계기
관왕
구슬땀
국가
국제
금

In [19]:
# 사람이 이해할 수 있는 형태로 코퍼스 사전 재구성 해보기 (term-frequency)
[[(dictionary[id], freq) for id, freq in cp] for cp in corpus]

[[('가운데', 1.0),
  ('갈등', 1.0),
  ('건물', 2.0),
  ('건축', 2.0),
  ('검토', 1.0),
  ('경우', 1.0),
  ('경종', 1.0),
  ('과도', 2.0),
  ('관계', 2.0),
  ('관련', 1.0),
  ('교육', 1.0),
  ('균열', 1.0),
  ('극단', 1.0),
  ('근접', 1.0),
  ('기관', 1.0),
  ('기대', 1.0),
  ('기피', 3.0),
  ('기회', 1.0),
  ('녹지', 2.0),
  ('님비', 3.0),
  ('묘지', 1.0),
  ('문제', 3.0),
  ('밀집', 1.0),
  ('발목', 1.0),
  ('발휘', 1.0),
  ('법령', 1.0),
  ('법원', 2.0),
  ('변경', 4.0),
  ('부당', 1.0),
  ('부족', 1.0),
  ('불허', 3.0),
  ('비용', 1.0),
  ('사실', 1.0),
  ('사유', 2.0),
  ('사회', 2.0),
  ('상대', 1.0),
  ('생활', 1.0),
  ('소', 1.0),
  ('소송', 1.0),
  ('숙박', 1.0),
  ('승소', 1.0),
  ('시설', 6.0),
  ('시장', 1.0),
  ('신청', 1.0),
  ('악영향', 1.0),
  ('여건', 1.0),
  ('역량', 1.0),
  ('올', 1.0),
  ('용도', 4.0),
  ('운영', 1.0),
  ('원고', 1.0),
  ('의견', 1.0),
  ('이기주의', 1.0),
  ('이번', 1.0),
  ('이용', 1.0),
  ('이유', 2.0),
  ('일견', 1.0),
  ('자연', 3.0),
  ('자체', 1.0),
  ('재판부', 1.0),
  ('정서', 4.0),
  ('정주', 1.0),
  ('정치', 1.0),
  ('정치력', 1.0),
  ('정치인', 3.0),
  ('제기', 1.0),
  ('제

In [20]:
# Author Topic Model 실행 : 있으면 load하고 없으면 model을 만들기
if not os.path.exists("./ATM/ATM_model"):
    model = AuthorTopicModel(corpus=corpus, num_topics=5, id2word=dictionary.id2token, \
                author2doc=author2doc, passes=100)
    
    model.save('./ATM/ATM_model')
else:
    model = AuthorTopicModel.load("./ATM/ATM_model")

## 2-1. ATM 토픽 결과

In [21]:
model.show_topic(0, topn=20)

[('체전', 0.018173922492746318),
 ('전국', 0.017889809759933196),
 ('시', 0.013258375938116743),
 ('통합', 0.01321228911022629),
 ('체육', 0.013158415252048956),
 ('센터', 0.012881434741229138),
 ('체험', 0.012060529414697718),
 ('장애인', 0.010932511735510613),
 ('개최', 0.010075800308608333),
 ('문학', 0.00966183177547858),
 ('시민', 0.008624580075587427),
 ('대회', 0.0077330467756409425),
 ('스포츠', 0.006267992265744149),
 ('예산', 0.006063151717297264),
 ('박람회', 0.005988328688487153),
 ('경기장', 0.0057961586251494375),
 ('행사', 0.005627790344551341),
 ('박홍', 0.00561072108784959),
 ('진행', 0.004812737251690187),
 ('운영', 0.004805568058437765)]

In [22]:
model.show_topic(1, topn=20)

[('홍어', 0.0689223742971396),
 ('흑', 0.030402844149564186),
 ('굴', 0.02438204013322472),
 ('인권', 0.02002294511573191),
 ('염전', 0.017313939061069608),
 ('천일염', 0.014587586038446931),
 ('자격증', 0.011009435057463633),
 ('숲', 0.010738551702981108),
 ('사람', 0.009036296434410363),
 ('소득', 0.008618270508589314),
 ('생산자', 0.008401647512083337),
 ('치유', 0.008216501874896951),
 ('학교', 0.007355661650517349),
 ('그림', 0.0073435395692910185),
 ('침해', 0.0071008694423847505),
 ('소금', 0.006383123142733161),
 ('제도', 0.006260545332750082),
 ('프로그램', 0.005641265782314314),
 ('힐링', 0.005540285416768315),
 ('손질', 0.005497830687548708)]

In [23]:
model.show_topic(2, topn=20)

[('지역', 0.013520932832863054),
 ('교육', 0.010316798916087689),
 ('사업', 0.009903697966032285),
 ('지원', 0.008256065206189468),
 ('섬', 0.006671240943649754),
 ('문화', 0.006116727554318248),
 ('추진', 0.005103733147892018),
 ('관광', 0.004272190985454216),
 ('기자', 0.004128425454516985),
 ('운영', 0.004004606722146373),
 ('주민', 0.003963142313952694),
 ('계획', 0.003892974806346321),
 ('학교', 0.0037738741537265297),
 ('말', 0.0037405072672388115),
 ('환경', 0.003717965863541973),
 ('청년', 0.003689931360420244),
 ('사회', 0.0035900525505453617),
 ('산업', 0.003566347513910724),
 ('제공', 0.003480024458752297),
 ('조성', 0.003347019372883522)]

In [24]:
model.show_topic(3, topn=20)

[('갯벌', 0.042601638882298454),
 ('세계', 0.03592037456777257),
 ('마을', 0.026300020980403196),
 ('유산', 0.019302243709192212),
 ('생태', 0.015068515975103992),
 ('자연', 0.014138974219920893),
 ('어업', 0.01280445757729726),
 ('생물', 0.012714563940934153),
 ('철새', 0.010250877252198533),
 ('바다', 0.009764777633814194),
 ('보전', 0.009232989707496234),
 ('양궁', 0.008824820377453448),
 ('중요', 0.008689361769699118),
 ('등재', 0.007705782978448859),
 ('길', 0.0075861811473574865),
 ('가치', 0.00753300613478815),
 ('사람', 0.007086347901759242),
 ('습지', 0.007063966219502897),
 ('국가', 0.00692318406669377),
 ('국내', 0.006786860785033078)]

In [25]:
# 토픽 라벨 지정. 
topic_labels = ["Topic0", "Topic1", "Topic2", "Topic3", "Topic4", "Topic5"]

In [52]:
# 토픽별로 topN 단어 확인하기.
# for topics in model.show_topics(model.num_topics):
for topic in model.show_topics(5):
    print('Label: ' + topic_labels[topic[0]])
    words = ''
    for word, prob in model.show_topic(topic[0], topn=20):
        words += word + ' '
    print('Words: ' + words)
    print()

Label: Topic0
Words: 체전 전국 시 통합 체육 센터 체험 장애인 개최 문학 시민 대회 스포츠 예산 박람회 경기장 행사 박홍 진행 운영 

Label: Topic1
Words: 홍어 흑 굴 인권 염전 천일염 자격증 숲 사람 소득 생산자 치유 학교 그림 침해 소금 제도 프로그램 힐링 손질 

Label: Topic2
Words: 지역 교육 사업 지원 섬 문화 추진 관광 기자 운영 주민 계획 학교 말 환경 청년 사회 산업 제공 조성 

Label: Topic3
Words: 갯벌 세계 마을 유산 생태 자연 어업 생물 철새 바다 보전 양궁 중요 등재 길 가치 사람 습지 국가 국내 

Label: Topic4
Words: 오전 무안 지역 군 군수 사업 주민 폐교 군민 교육 농가 공항 지원 오후 근로자 이전 센터 계획 농업 지급 



## 2-2. 지역과 토픽

In [27]:
# model.get_author_topics("무안")

[(2, 0.8974525374942576), (4, 0.09818651475718926)]

In [55]:
model["무안"]

[(2, 0.8974525374942576), (4, 0.09818651475718926)]

In [56]:
model["신안"]

[(2, 0.9543677936426842), (3, 0.03848959483580188)]

In [57]:
model["목포"]

[(0, 0.03491947364280464), (2, 0.9533137511922094), (3, 0.010300124654104039)]

In [63]:
# 사용자별로 토픽 분포 확인하기.
def show_author(name):
    print('\n%s' % name) # 지역명
    print('\nDocs:', model.author2doc[name])
    print('\nTopics:')
    pprint([(topic_labels[topic[0]], topic[1]) for topic in model[name]])

In [64]:
show_author('무안')


무안

Docs: [1679, 1680, 1681, 1682, 1683, 1684, 1685, 1686, 1687, 1688, 1689, 1690, 1691, 1692, 1693, 1694, 1695, 1696, 1697, 1698, 1699, 1700, 1701, 1702, 1703, 1704, 1705, 1706, 1707, 1708, 1709, 1710, 1711, 1712, 1713, 1714, 1715, 1716, 1717, 1718, 1719, 1720, 1721, 1722, 1723, 1724, 1725, 1726, 1727, 1728, 1729, 1730, 1731, 1732, 1733, 1734, 1735, 1736, 1737, 1738, 1739, 1740, 1741, 1742, 1743, 1744, 1745, 1746, 1747, 1748, 1749, 1750, 1751, 1752, 1753, 1754, 1755, 1756, 1757, 1758, 1759, 1760, 1761, 1762, 1763, 1764, 1765, 1766, 1767, 1768, 1769, 1770, 1771, 1772, 1773, 1774, 1775, 1776, 1777, 1778, 1779, 1780, 1781, 1782, 1783, 1784, 1785, 1786, 1787, 1788, 1789, 1790, 1791, 1792, 1793, 1794, 1795, 1796, 1797, 1798, 1799, 1800, 1801, 1802, 1803, 1804, 1805, 1806, 1807, 1808, 1809, 1810, 1811, 1812, 1813, 1814, 1815, 1816, 1817, 1818, 1819, 1820, 1821, 1822, 1823, 1824, 1825, 1826, 1827, 1828, 1829, 1830, 1831, 1832, 1833, 1834, 1835, 1836, 1837, 1838, 1839, 1840, 1841, 1842, 1843

In [65]:
show_author('신안')


신안

Docs: [2917, 2918, 2919, 2920, 2921, 2922, 2923, 2924, 2925, 2926, 2927, 2928, 2929, 2930, 2931, 2932, 2933, 2934, 2935, 2936, 2937, 2938, 2939, 2940, 2941, 2942, 2943, 2944, 2945, 2946, 2947, 2948, 2949, 2950, 2951, 2952, 2953, 2954, 2955, 2956, 2957, 2958, 2959, 2960, 2961, 2962, 2963, 2964, 2965, 2966, 2967, 2968, 2969, 2970, 2971, 2972, 2973, 2974, 2975, 2976, 2977, 2978, 2979, 2980, 2981, 2982, 2983, 2984, 2985, 2986, 2987, 2988, 2989, 2990, 2991, 2992, 2993, 2994, 2995, 2996, 2997, 2998, 2999, 3000, 3001, 3002, 3003, 3004, 3005, 3006, 3007, 3008, 3009, 3010, 3011, 3012, 3013, 3014, 3015, 3016, 3017, 3018, 3019, 3020, 3021, 3022, 3023, 3024, 3025, 3026, 3027, 3028, 3029, 3030, 3031, 3032, 3033, 3034, 3035, 3036, 3037, 3038, 3039, 3040, 3041, 3042, 3043, 3044, 3045, 3046, 3047, 3048, 3049, 3050, 3051, 3052, 3053, 3054, 3055, 3056, 3057, 3058, 3059, 3060, 3061, 3062, 3063, 3064, 3065, 3066, 3067, 3068, 3069, 3070, 3071, 3072, 3073, 3074, 3075, 3076, 3077, 3078, 3079, 3080, 3081

In [66]:
show_author('목포')


목포

Docs: [0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 20, 21, 22, 23, 24, 25, 26, 27, 28, 29, 30, 31, 32, 33, 34, 35, 36, 37, 38, 39, 40, 41, 42, 43, 44, 45, 46, 47, 48, 49, 50, 51, 52, 53, 54, 55, 56, 57, 58, 59, 60, 61, 62, 63, 64, 65, 66, 67, 68, 69, 70, 71, 72, 73, 74, 75, 76, 77, 78, 79, 80, 81, 82, 83, 84, 85, 86, 87, 88, 89, 90, 91, 92, 93, 94, 95, 96, 97, 98, 99, 100, 101, 102, 103, 104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116, 117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129, 130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142, 143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155, 156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168, 169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 180, 181, 182, 183, 184, 185, 186, 187, 188, 189, 190, 191, 192, 193, 194, 195, 196, 197, 198, 199, 200, 201, 202, 203, 204, 205, 206, 207, 208, 209, 210, 211, 212, 213, 214, 215, 216, 217, 218, 219

In [70]:
# 종합해서 보기
[model.get_author_topics(author) for author in model.id2author.values()]

[[(0, 0.03491947364280464),
  (2, 0.9533137511922094),
  (3, 0.010300124654104039)],
 [(2, 0.8974525374942576), (4, 0.09818651475718926)],
 [(2, 0.9543677936426842), (3, 0.03848959483580188)]]

In [76]:
# 토픽별 지역 순위 확인

In [74]:
all_list = list(model.id2author.values())
tmp_l = []
for a in all_list:
    for topic in model[a]:
        tmp_l.append([a, topic[0], topic[1]])

In [79]:
tmp_df = pd.DataFrame(tmp_l)
tmp_df.columns = ['author', 'topic_id', 'prob']
tmp_df = tmp_df[['topic_id','author', 'prob']]

In [81]:
tmp_df.sort_values(['topic_id', 'prob'], inplace=True)

In [73]:
tmp_df = pd.DataFrame(tmp_l)
tmp_df.columns = ['author', 'topic_id', 'prob']
tmp_df = tmp_df[['topic_id','author', 'prob']]
tmp_df.sort_values(['topic_id', 'prob'], inplace=True)
tmp_df.reset_index(drop=True, inplace=True)
tmp_df_rank = tmp_df.groupby(['topic_id']).tail(3)
tmp_df_rank['rank'] = model.num_topics * [3 - i for i in range(3)]
tmp_df_rank.sort_values(['topic_id', 'rank'], inplace=True)
tmp_df_rank

ValueError: Length of values (15) does not match length of index (7)

In [27]:
# 토픽별 하위 10개 판매처
a_list = list(model.id2author.values())
tmp_l = []
for a in a_list:
    for topic in model[a]:
        tmp_l.append([a, topic[0], topic[1]])


tmp_df = pd.DataFrame(tmp_l)
tmp_df.columns = ['author', 'topic_id', 'prob']
tmp_df = tmp_df[['topic_id','author', 'prob']]
tmp_df.sort_values(['topic_id', 'prob'], inplace=True, ascending=False)
tmp_df.reset_index(drop=True, inplace=True)
tmp_df_top10 = tmp_df.groupby(['topic_id']).tail(10)
tmp_df_top10['rank'] = model.num_topics * [10 - i for i in range(10)]
tmp_df_top10.sort_values(['topic_id', 'rank'], inplace=True)
tmp_df_top10

C:\Users\user\AppData\Local\Temp\ipykernel_25840\3570404004.py:15: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  tmp_df_top10['rank'] = model.num_topics * [10 - i for i in range(10)]
C:\Users\user\AppData\Local\Temp\ipykernel_25840\3570404004.py:16: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  tmp_df_top10.sort_values(['topic_id', 'rank'], inplace=True)


topic_id          author      prob  rank
554         0           롯데백화점  0.010588     1
553         0       주식회사 에이비즈  0.012354     2
552         0    LG전자인증점 죽산정보  0.012365     3
551         0        HP 공식파트너  0.014090     4
550         0              옥션  0.015883     5
549         0           가온누리m  0.018501     6
548         0            아이코다  0.018672     7
547         0         마스터다이어트  0.019972     8
546         0      삼성공식파트너 코잇  0.020232     9
545         0          열두달컴퍼니  0.021344    10
437         1           더좋은친구  0.010053     1
436         1           롯데백화점  0.010514     2
435         1           롯데홈쇼핑  0.010925     3
434         1      삼성공식파트너 코잇  0.011323     4
433         1   LG전자인증점 티앤티정보  0.011644     5
432         1    LG전자인증점 죽산정보  0.012051     6
431         1  LG전자인증점 OK오아시스  0.012314     7
430         1           러블리가전  0.012740     8
429         1   LG전자인증점 대원CTS  0.013807     9
428         1        HP 공식파트너  0.013934    10
344         2           프로씨앤씨  0.012301     1
343         2            삼성닷컴  0.029152     2
342         2           성화씨앤씨  0.033594     3
341         2          CJ온스타일  0.040671     4
340         2            아이피몰  0.100295     5
339         2           김 특 가  0.261131     6
338         2      꿈꾸는다락방2015  0.269500     7
337         2            전자랜드  0.279016     8
336         2           가온누리m  0.338961     9
335         2           SSG닷컴  0.360107    10
216         3           롯데백화점  0.010669     1
215         3       주식회사 에이비즈  0.012196     2
214         3           러블리가전  0.012928     3
213         3          그래미플러스  0.015862     4
212         3  윤스샵 yoons shop  0.015960     5
211         3            아이코다  0.018906     6
210         3            EEAN  0.019181     7
209         3         마스터다이어트  0.019968     8
208         3          열두달컴퍼니  0.021290     9
207         3           광림씨엔씨  0.024712    10
102         4    LG전자인증점 엘시인포  0.011131     1
101         4       주식회사 에이비즈  0.012054     2
100         4    LG전자인증점 죽산정보  0.012133     3
99          4  노트북공식인증점 메인CNS  0.013379     4
98          4        HP 공식파트너  0.013934     5
97          4            홈앤쇼핑  0.014347     6
96          4        PANTACOM  0.014912     7
95          4             원이텍  0.015433     8
94          4          그래미플러스  0.015613     9
93          4           노트프라자  0.015756    10

In [28]:
# author-topic 분포 만들기
#author_vecs = [model[author] for author in model.id2author.values()]
author_vecs = [model.get_author_topics(market) for market in model.id2author.values()]
 
def similarity(vec1, vec2):
    # vec1, vec2 사이의 hellinger similarity 구하기.
    dist = hellinger(matutils.sparse2full(vec1, model.num_topics), \
                              matutils.sparse2full(vec2, model.num_topics))
    sim = 1.0 / (1.0 + dist)
    return sim
 
def get_sims(vec):
    # 각 사용자들 사이의 similarity pair 구하기.
    sims = [similarity(vec, vec2) for vec2 in author_vecs]
    return sims
 
def get_table(name, top_n=10, smallest_author=1): # top_n은 나랑 비슷한 저자 수
    """
    주어진 사용자에 대해서 topN 사람만큼 유사도를 정렬해서 table을 출력하는 함수입니다.
    """
    
    # 유사도 측정하기
    sims = get_sims(model.get_author_topics(name))
 
    # 저자별 정보 정렬하기
    table = []
    for elem in enumerate(sims):
        author_name = model.id2author[elem[0]]
        sim = elem[1]
        # 저자가 몇 개의 문서에 등장했는지를 알 수 있음
        author_size = len(model.author2doc[author_name])
        if author_size >= smallest_author:
            table.append((author_name, sim, author_size)) # table에 유저에 대한 정보를 넣어줌
            
    # 사용자 패턴 분석 결과를 Dataframe으로 만들기
    df = pd.DataFrame(table, columns=['Author', 'Score', 'Size'])
    df = df.sort_values('Score', ascending=False)[:top_n] # ascending을 False로 해줘야함(유사성을 찾기 위함)
    
    return df

In [29]:
# 마켓별 패턴 검증 : 유사한 판매처 확인
get_table('LG전자인증점 디지털대박')

Author     Score  Size
23    LG전자인증점 디지털대박  1.000000    48
31         LG정식총판매점  0.960926    64
30    LG전자인증점 티앤티정보  0.934469    50
109     주식회사 퍼스트나인즈  0.905236    29
83           아이즈팩토리  0.900219    10
39           가온해씨앤씨  0.896022    30
46   노트북공식인증점 메인CNS  0.884770    51
49           더가치스토어  0.884493    21
42           그래미플러스  0.882205     3
14     LG 노트북 공식인증점  0.881850    18